In [0]:
# Import required libraries
from pyspark.sql import functions as F

# Load October raw data
october_df = spark.read.csv("/Volumes/workspace/advecom/advecom_data/2019-Oct.csv", header=True, inferSchema=True)

# Create user feature dataframe, with necessary features only 
user_features_df = october_df.filter(F.col("price") > 0) \
    .filter("user_id IS NOT NULL") \
    .dropDuplicates(["user_id","product_id","event_type","event_time"]) \
    .groupBy("user_id") \
    .agg(
        F.sum(
            F.when(F.col("event_type")=="view",1)
            .otherwise(0)
        ).alias("total_views"),
        F.sum(
            F.when(F.col("event_type")=="cart",1)
            .otherwise(0)
        ).alias("total_cart"),
        F.sum(
            F.when(F.col("event_type")=="purchase",1)
            .otherwise(0)
        ).alias("total_purchases"),
        F.avg("price").alias("avg_price"),
        F.count("user_id").alias("total_events"),
        F.sum(F.when(F.col("event_type")=="purchase", F.col("price")).otherwise(0)).alias("total_spent")
    )
    
# Check user features
display(user_features_df.limit(5))

user_id total_views total_cart total_purchases avg_price total_events total_spent 516407514 19 2 1 224.08909090909094 22 231.64 547701060 14 2 0 1119.1575 16 0.0 514555296 65 0 1 283.03409090909093 66 244.28 555846537 23 2 2 203.63814814814816 27 368.04 513383856 11 0 0 724.3663636363636 11 0.0

In [0]:
# Create target label dataframe from user features
labeled_df = user_features_df.withColumn(
    "label",
    F.when(F.col("total_purchases")>0,1)
    .otherwise(0)
    )

# Check labeled dataframe
display(labeled_df)

user_id total_views total_cart total_purchases avg_price total_events total_spent label 516407514 19 2 1 224.08909090909094 22 231.64 1 547701060 14 2 0 1119.1575 16 0.0 0 514555296 65 0 1 283.03409090909093 66 244.28 1 555846537 23 2 2 203.63814814814816 27 368.04 1 513383856 11 0 0 724.3663636363636 11 0.0 0 519148299 11 1 3 248.33800000000005 15 483.45000000000005 1 516264626 8 0 0 392.1275 8 0.0 0 515936492 30 0 0 479.965 30 0.0 0 521328224 13 0 0 157.47384615384615 13 0.0 0 535611590 10 0 0 7.726999999999999 10 0.0 0 513614549 24 0 0 273.6620833333333 24 0.0 0 532829938 65 0 0 884.2098461538462 65 0.0 0 518808581 14 1 0 475.2893333333333 15 0.0 0 547727222 30 1 0 215.3932258064516 31 0.0 0 551300931 20 0 0 246.74449999999996 20 0.0 0 516430318 54 0 0 137.92611111111108 54 0.0 0 518468442 2 0 0 386.08 2 0.0 0 515880464 41 0 1 541.437380952381 42 274.91 1 555970113 1 0 0 952.63 1 0.0 0 547718922 172 2 0 303.0639655172414 174 0.0 0 512759337 16 0 0 148.04000000000002 16 0.0 0 555587727 33 0 0 256.6248484848485 33 0.0 0 513693255 286 0 0 662.5820629370629 286 0.0 0 515780527 99 0 0 127.36010101010102 99 0.0 0 513236719 58 0 0 276.84586206896546 58 0.0 0 544268631 38 0 1 302.8282051282051 39 574.02 1 549277997 150 0 3 76.1002614379085 153 266.4 1 548098636 24 0 0 238.55708333333334 24 0.0 0 513246630 89 1 0 474.9006666666667 90 0.0 0 548512468 2 0 0 460.5 2 0.0 0 543232438 108 1 1 283.26227272727266 110 88.79 1 514085467 118 0 0 420.0113559322033 118 0.0 0 512769367 57 1 0 198.97706896551728 58 0.0 0 555432662 11 0 0 135.64090909090908 11 0.0 0 530850692 52 0 0 104.96615384615384 52 0.0 0 542189044 19 0 0 485.00526315789466 19 0.0 0 555907274 2 0 0 679.935 2 0.0 0 514508014 53 4 2 86.27898305084747 59 86.48 1 529400022 29 0 0 251.7779310344828 29 0.0 0 516244341 26 0 0 31.196538461538463 26 0.0 0 556013037 11 0 0 139.97545454545454 11 0.0 0 556010139 3 1 1 359.03 5 359.03 1 513593317 56 0 0 507.25232142857146 56 0.0 0 523704871 12 0 0 167.625 12 0.0 0 516581972 24 0 0 18.48541666666667 24 0.0 0 520663096 17 0 0 223.75176470588235 17 0.0 0 514142848 8 0 0 47.989999999999995 8 0.0 0 523914128 7 0 1 198.5375 8 72.05 1 555578156 20 0 0 344.6925 20 0.0 0 536111756 17 0 0 85.5335294117647 17 0.0 0 555868154 7 0 1 40.176249999999996 8 38.33 1 553069142 3 0 0 191.6233333333333 3 0.0 0 526975969 30 0 0 123.39666666666669 30 0.0 0 515897473 84 0 0 173.7134523809524 84 0.0 0 552337325 35 0 0 240.06971428571424 35 0.0 0 526949848 53 0 0 290.73660377358493 53 0.0 0 555194108 25 0 0 208.5776 25 0.0 0 555813647 5 0 0 96.31 5 0.0 0 513535007 86 5 2 153.3512903225807 93 421.83 1 555513808 14 0 0 167.74857142857144 14 0.0 0 545005886 9 2 4 213.28133333333335 15 867.11 1 555611088 42 0 0 283.5261904761905 42 0.0 0 513834734 304 1 2 90.18042345276872 307 206.17 1 517394514 5 2 1 130.25 8 130.25 1 555481419 68 0 0 343.6760294117647 68 0.0 0 547845430 5 0 0 424.462 5 0.0 0 513902038 8 0 0 1410.9437500000001 8 0.0 0 534848118 60 0 0 167.871 60 0.0 0 512860682 14 5 4 554.9973913043478 23 1010.72 1 520935079 2 0 0 1361.675 2 0.0 0 513160008 38 0 0 94.22736842105263 38 0.0 0 537801031 7 0 0 879.7871428571428 7 0.0 0 521453921 132 5 2 146.12762589928056 139 136.42000000000002 1 555818154 13 0 0 269.56384615384616 13 0.0 0 512451508 86 2 0 315.0459090909091 88 0.0 0 554054988 16 0 0 523.5699999999999 16 0.0 0 548099509 26 1 0 490.5885185185186 27 0.0 0 525369631 10 0 1 235.8290909090909 11 130.7 1 513203821 23 0 0 84.3286956521739 23 0.0 0 548463233 15 0 0 153.03066666666666 15 0.0 0 555860367 13 0 1 50.65571428571429 14 47.36 1 555557656 36 0 2 192.49131578947367 38 261.4 1 545569045 5 0 1 573.8166666666667 6 350.71 1 514525373 114 4 2 239.17366666666666 120 617.22 1 525447911 71 3 0 402.0275675675676 74 0.0 0 512569646 80 0 0 97.91425 80 0.0 0 513294052 12 0 0 514.4574999999999 12 0.0 0 556014248 12 0 0 648.8575 12 0.0 0 524457561 122 2 1 181.8868 125 197.95 1 535544747 8 1 1 273.348 10 192.23 1 518039319 51 0 0 122.99196078431373 51 0.0 0 555881119 20

In [0]:
# Check distribution of labels
labeled_df.groupBy("label").count().show()

+-----+-------+
|label|  count|
+-----+-------+
|    1| 347118|
|    0|2674317|
+-----+-------+



In [0]:
# Create two dataframes for purchase and non-purchase, and then combine them with a smaller fraction of non purchase. As a result the model will be trained on a balanced dataset.
purchase_df = labeled_df.filter("label=1")

non_purchase_df = labeled_df.filter("label=0") \
.sample(fraction=0.13)

balanced_df = purchase_df.union(non_purchase_df)

balanced_df.groupBy("label").count().show()

+-----+------+
|label| count|
+-----+------+
|    1|347118|
|    0|347427|
+-----+------+



In [0]:
# Import required libraries
from pyspark.ml.feature import VectorAssembler

# Create features vector for ML
assembler = VectorAssembler(
    inputCols=[
        "total_views",
        "total_cart",
        "total_spent",
        "total_events",
        "avg_price"
    ],
    outputCol="features"
)

# Create model dataframe with features and label
model_df = assembler.transform(balanced_df).select("features","label")

display(model_df)

features label {"type":"1","size":null,"indices":null,"values":["19.0","2.0","231.64","22.0","224.08909090909094"]} 1 {"type":"1","size":null,"indices":null,"values":["65.0","0.0","244.28","66.0","283.03409090909093"]} 1 {"type":"1","size":null,"indices":null,"values":["23.0","2.0","368.04","27.0","203.63814814814816"]} 1 {"type":"1","size":null,"indices":null,"values":["11.0","1.0","483.45000000000005","15.0","248.33800000000005"]} 1 {"type":"1","size":null,"indices":null,"values":["41.0","0.0","274.91","42.0","541.437380952381"]} 1 {"type":"1","size":null,"indices":null,"values":["38.0","0.0","574.02","39.0","302.8282051282051"]} 1 {"type":"1","size":null,"indices":null,"values":["150.0","0.0","266.4","153.0","76.1002614379085"]} 1 {"type":"1","size":null,"indices":null,"values":["108.0","1.0","88.79","110.0","283.26227272727266"]} 1 {"type":"1","size":null,"indices":null,"values":["53.0","4.0","86.48","59.0","86.27898305084747"]} 1 {"type":"1","size":null,"indices":null,"values":["3.0","1.0","359.03","5.0","359.03"]} 1 {"type":"1","size":null,"indices":null,"values":["7.0","0.0","72.05","8.0","198.5375"]} 1 {"type":"1","size":null,"indices":null,"values":["7.0","0.0","38.33","8.0","40.176249999999996"]} 1 {"type":"1","size":null,"indices":null,"values":["86.0","5.0","421.83","93.0","153.3512903225807"]} 1 {"type":"1","size":null,"indices":null,"values":["9.0","2.0","867.11","15.0","213.28133333333335"]} 1 {"type":"1","size":null,"indices":null,"values":["304.0","1.0","206.17","307.0","90.18042345276872"]} 1 {"type":"1","size":null,"indices":null,"values":["5.0","2.0","130.25","8.0","130.25"]} 1 {"type":"1","size":null,"indices":null,"values":["14.0","5.0","1010.72","23.0","554.9973913043478"]} 1 {"type":"1","size":null,"indices":null,"values":["132.0","5.0","136.42000000000002","139.0","146.12762589928056"]} 1 {"type":"1","size":null,"indices":null,"values":["10.0","0.0","130.7","11.0","235.8290909090909"]} 1 {"type":"1","size":null,"indices":null,"values":["13.0","0.0","47.36","14.0","50.65571428571429"]} 1 {"type":"1","size":null,"indices":null,"values":["36.0","0.0","261.4","38.0","192.49131578947367"]} 1 {"type":"1","size":null,"indices":null,"values":["5.0","0.0","350.71","6.0","573.8166666666667"]} 1 {"type":"1","size":null,"indices":null,"values":["114.0","4.0","617.22","120.0","239.17366666666666"]} 1 {"type":"1","size":null,"indices":null,"values":["122.0","2.0","197.95","125.0","181.8868"]} 1 {"type":"1","size":null,"indices":null,"values":["8.0","1.0","192.23","10.0","273.348"]} 1 {"type":"1","size":null,"indices":null,"values":["32.0","0.0","1342.48","34.0","339.5894117647059"]} 1 {"type":"1","size":null,"indices":null,"values":["17.0","6.0","348.44","25.0","183.10280000000003"]} 1 {"type":"1","size":null,"indices":null,"values":["7.0","13.0","252.91","21.0","244.06238095238092"]} 1 {"type":"1","size":null,"indices":null,"values":["8.0","1.0","161.9","10.0","156.15400000000002"]} 1 {"type":"1","size":null,"indices":null,"values":["132.0","1.0","30.09","134.0","366.4476119402985"]} 1 {"type":"1","size":null,"indices":null,"values":["5.0","4.0","74.36","10.0","74.36"]} 1 {"type":"1","size":null,"indices":null,"values":["33.0","1.0","253.02","35.0","314.4851428571428"]} 1 {"type":"1","size":null,"indices":null,"values":["13.0","1.0","37.07","15.0","64.92"]} 1 {"type":"1","size":null,"indices":null,"values":["29.0","8.0","3695.22","42.0","700.3992857142856"]} 1 {"type":"1","size":null,"indices":null,"values":["63.0","0.0","312.49","64.0","403.48468749999995"]} 1 {"type":"1","size":null,"indices":null,"values":["35.0","0.0","385.85","36.0","269.87194444444447"]} 1 {"type":"1","size":null,"indices":null,"values":["81.0","0.0","594.61","83.0","241.82240963855423"]} 1 {"type":"1","size":null,"indices":null,"values":["27.0","1.0","601.69","31.0","359.45258064516133"]} 1 {"type":"1","size":null,"indices":null,"values":["47.0","1.0","755.98","50.0","167.0454"]} 1 {"type":"1","size":null,"indices":null,"values":["20.0","1.0

In [0]:
# Split data into training and test
train_df, test_df = model_df.randomSplit([0.8,0.2], seed=7)

# Check label distribution across train and test
train_df.groupBy("label").count().show()
test_df.groupBy("label").count().show() 

+-----+------+
|label| count|
+-----+------+
|    1|277727|
|    0|277757|
+-----+------+

+-----+-----+
|label|count|
+-----+-----+
|    1|69391|
|    0|69670|
+-----+-----+



In [0]:
# Import required libraries
import mlflow
import mlflow.spark
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.evaluation import BinaryClassificationEvaluator
# Log Logistic Regression model with MLflow
with mlflow.start_run(run_name="log_reg_model"):
        
    # Initialize logistic regression model
    lr = LogisticRegression(
        featuresCol="features",
        labelCol="label"
    )
    # Fit model on training data
    lr_model = lr.fit(train_df)
    # Make predictions on test data
    lr_pred = lr_model.transform(test_df)
    # Initialize binary classification evaluator
    evaluator = BinaryClassificationEvaluator(
        labelCol="label"
    )
    lr_auc = evaluator.evaluate(lr_pred) # Calculate AUC

    mlflow.log_param("model_type", "Logistic Regression") # Log model type
    mlflow.log_metric("AUC", lr_auc) # Log metric as AUC
    mlflow.spark.log_model(spark_model=lr_model, # Log model
                           artifact_path="logistic_model", # Specify artifact path
                           dfs_tmpdir="/Volumes/workspace/advecom/advecom_data/mlflowlog") # Specify temp directory
    print("Logistic Regression AUC:", lr_auc)

2026/02/26 19:24:53 WARNING mlflow.utils.requirements_utils: Found pyspark version (4.0.0+databricks.connect.17.3.2) contains a local version label (+databricks.connect.17.3.2). MLflow logged a pip requirement for this package as 'pyspark==4.0.0' without the local version label to make it installable from PyPI. To specify pip requirements containing local version labels, please use `conda_env` or `pip_requirements`.
2026/02/26 19:24:55 WARNING mlflow.utils.environment: Encountered an unexpected error while inferring pip requirements (model URI: /local_disk0/user_tmp_data/spark-6699d492-c72d-41ec-8443-6e/tmplivsi55p/model, flavor: spark). Fall back to return ['pyspark==4.0.0']. Set logging level to DEBUG to see the full traceback. 
2026/02/26 19:24:55 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.


Logistic Regression AUC: 0.9999998245930102


In [0]:

 # Import required libraries
from pyspark.ml.classification import RandomForestClassifier
# Log Random Forest Classifier model with MLflow
with mlflow.start_run(run_name="rf_classifier"):      
    # Initialize random forest model
    rf = RandomForestClassifier(
        featuresCol="features",
        labelCol="label",
        numTrees=20,
        maxDepth=5
    )
    # Fit model on training data
    rf_model = rf.fit(train_df)
    # Make predictions on test data
    rf_pred = rf_model.transform(test_df)
    # Initialize binary classification evaluator
    evaluator = BinaryClassificationEvaluator(
        labelCol="label"
    )
    rf_auc = evaluator.evaluate(rf_pred) # Calculate AUC
    mlflow.log_param("model_type", "Random Forest Classifier") # log model type
    mlflow.log_param("numTrees", rf.getNumTrees) # log parameter number of trees
    mlflow.log_param("maxDepth", rf.getMaxDepth()) # log parameter max depth
    
    mlflow.log_metric("AUC", rf_auc) # log metric as AUC
    mlflow.spark.log_model(spark_model=rf_model, # log model
                           artifact_path="random_forest_classifier", # specify artifact path
                           dfs_tmpdir="/Volumes/workspace/advecom/advecom_data/mlflowlog") # specify temp directory

    print("Random Forest Classifier AUC:", rf_auc)

2026/02/26 19:27:29 WARNING mlflow.utils.requirements_utils: Found pyspark version (4.0.0+databricks.connect.17.3.2) contains a local version label (+databricks.connect.17.3.2). MLflow logged a pip requirement for this package as 'pyspark==4.0.0' without the local version label to make it installable from PyPI. To specify pip requirements containing local version labels, please use `conda_env` or `pip_requirements`.
2026/02/26 19:27:32 WARNING mlflow.utils.environment: Encountered an unexpected error while inferring pip requirements (model URI: /local_disk0/user_tmp_data/spark-6699d492-c72d-41ec-8443-6e/tmp10jc3ojb/model, flavor: spark). Fall back to return ['pyspark==4.0.0']. Set logging level to DEBUG to see the full traceback. 
2026/02/26 19:27:32 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.


Random Forest Classifier AUC: 1.0


In [0]:
print("Logistic Regression AUC:", lr_auc)
print("Random Forest Classifier AUC:", rf_auc)

Logistic Regression AUC: 0.9999998245930102
Random Forest Classifier AUC: 1.0
